In [2]:
from cmath import nan
from math import isnan
import difflib
from tkinter.tix import COLUMN 
import pandas as pd
import numpy as np
import json
from pathlib import Path
import lib.pdfield as pdfield
from matplotlib import pyplot as plt


In [2]:
%reload_ext autoreload
%autoreload 2
pdfield.detect_and_rename_qr('P:/UrukLarge/WES_paleoenvi/Proben_Bilder7')

In [3]:
%reload_ext autoreload
%autoreload 2

### Setup connection to Field-database-server based on config.json file ###
config = pdfield.loadconfigs('config\config.json')
api = pdfield.couchDB_APIs(config)

In [6]:
### Import all documents from Target Field-database ###
targetDOCs= pdfield.getAllDocs(api)
targetDF, docfields  = pdfield.allDocsToDf(targetDOCs)


The database uruk contains 26908 docs.
This is round 1offset : 0
This is round 2offset : 10000
This is round 3offset : 20000
26908
['created', 'modified', '_id', '_rev', 'project', 'resource.identifier']


In [20]:
%reload_ext autoreload
%autoreload 2
photos = targetDF[targetDF['type']=='Photo']
photosundup = photos.apply(pdfield.simpleunduplicateSelection,alldf=targetDF, axis=1)
DOCSphotos = pdfield.DFtoDOCv1(DF=photosundup, docfields=docfields)
DOCS2 = {'docs':[]}
for doc in DOCSphotos['docs']:
    doc = pdfield.addModifiedEntry(doc)
    DOCS2['docs'].append(doc)
pretty_json = json.dumps(DOCS2, indent=2)
print(pretty_json)

Index(['identifier', 'relations', 'id', 'geometry', 'type', 'height',
       'literature', 'originalFilename', 'shortDescription', 'width',
       ...
       'institution', 'projectSupervisor', 'campaigns', 'epsgId', 'created',
       'modified', '_id', '_rev', 'project', 'resource.identifier'],
      dtype='object', length=119)
{
  "docs": [
    {
      "created": {
        "user": "Max Haibt",
        "date": "2019-03-01T17:03:36.098Z"
      },
      "modified": [
        {
          "user": "Script mhaibt",
          "date": "2023-03-24T05:43:34.591Z"
        },
        {
          "user": "Script mhaibt",
          "date": "2023-03-24T05:46:34.656Z"
        },
        {
          "user": "Script mhaibt",
          "date": "2023-03-24T05:48:44.211Z"
        },
        {
          "user": "Script mhaibt",
          "date": "2023-03-24T05:52:22.433Z"
        },
        {
          "user": "Script mhaibt",
          "date": "2023-03-24T06:04:26.114Z"
        },
        {
          "use

In [21]:
pdfield.bulkSaveChanges(api, DOC=DOCS2, db_name='uruk')

<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
<Response [201]>
Documents uploaded


In [6]:
%reload_ext autoreload
%autoreload 2
photos = targetDF[targetDF['type']=='Photo']
unlikedPhotos = pdfield.getUnlinkedImages(photos)
print(unlikedPhotos['identifier'])
photosmatch = unlikedPhotos.rename(columns={'id':'PhotoId'})
#samples = targetDF[targetDF['type']=='Sample']
samples = targetDF
#print(samples['relations'])
samplesWithPhotos = pdfield.combineFramesByFixId(inputdf=photosmatch,targetdf = samples ,id ='identifier',combinefields = ['PhotoId'], replacemap={'.JPG':'','.png':'','.jpg':''})
samplesWithPhotos = samplesWithPhotos[samplesWithPhotos['PhotoId'].notnull()]
#samplesWithPhotos =  samplesWithPhotos.apply(pdfield.createDictColumn,outputfield='relations',axis=1)
samplesWithPhotos = samplesWithPhotos.apply(pdfield.createRelationFromField, inputfield= 'PhotoId', relation ='isDepictedIn', axis=1)
samplesWithPhotos.drop(columns=['PhotoId'], inplace=True)
print(samplesWithPhotos['identifier'])
samplesmatch = samples.rename(columns={'id':'SampleId'})
PhotoswithSamples = pdfield.combineFramesByFixId(inputdf=samplesmatch,targetdf = unlikedPhotos ,id ='identifier',combinefields = ['SampleId'], replacemap={'.JPG':'','.png':'','.jpg':''})
PhotoswithSamples = PhotoswithSamples[PhotoswithSamples['SampleId'].notnull()]
#PhotoswithSamples =  PhotoswithSamples.apply(pdfield.createDictColumn,outputfield='relations',axis=1)
PhotoswithSamples = PhotoswithSamples.apply(pdfield.createRelationFromField, inputfield= 'SampleId', relation ='depicts', axis=1)
PhotoswithSamples.drop(columns=['SampleId'], inplace=True)
PhotoswithSamples['identifier'] = PhotoswithSamples['identifier']+'.png'

174      WESid_34_col_dia1.JPG
194             WESid_3393.png
230             WESid_3337.png
273             WESid_3329.png
302             WESid_3318.JPG
                 ...          
26315           WESid_3259.png
26427           WESid_3211.png
26704           WESid_3356.png
26832    WESid_15_col_dia1.JPG
26846           WESid_3227.JPG
Name: identifier, Length: 324, dtype: object
41              WESid_3183
122             WESid_3183
174      WESid_34_col_dia1
194             WESid_3393
226             WESid_3318
               ...        
26438           WESid_3211
26715           WESid_3356
26824           WESid_3289
26843    WESid_15_col_dia1
26857           WESid_3227
Name: identifier, Length: 534, dtype: object


In [7]:
%reload_ext autoreload
%autoreload 2
DOCSsamples = pdfield.DFtoDOCv1(DF=samplesWithPhotos, docfields=docfields)
DOCSphotos = pdfield.DFtoDOCv1(DF=PhotoswithSamples, docfields=docfields)
DOCS2 = {'docs':[]}
for doc in DOCSsamples['docs']:
    doc = pdfield.addModifiedEntry(doc)
    DOCS2['docs'].append(doc)
for doc in DOCSphotos['docs']:
    doc = pdfield.addModifiedEntry(doc)
    DOCS2['docs'].append(doc)
pretty_json = json.dumps(DOCS2, indent=2)

print(pretty_json)

Index(['identifier', 'relations', 'id', 'geometry', 'type', 'height',
       'literature', 'originalFilename', 'shortDescription', 'width',
       ...
       'institution', 'projectSupervisor', 'campaigns', 'epsgId', 'created',
       'modified', '_id', '_rev', 'project', 'resource.identifier'],
      dtype='object', length=119)
Index(['AmountOfDebitageSurfaces', 'AmountOfDrillinbitsOntheTool',
       'ApplicationComparisonCompendia',
       'ApplicationComparisonCompendiadetail', 'ContactMaterial',
       'CorticalSurface', 'DecorationComparisonCompendia',
       'DecorationComparisonCompendiadetail', 'Drawing', 'DrawingId',
       ...
       'temper', 'temperAmount', 'temperParticles', 'transparency',
       'treatment', 'type', 'valuelists', 'vesselForm', 'vesselpart', 'width'],
      dtype='object', length=119)
{
  "docs": [
    {
      "created": {
        "user": "DAI-OA-185",
        "date": "2023-03-05T13:18:44.728Z"
      },
      "modified": [
        {
          "user": "DAI

In [29]:
pdfield.bulkSaveChanges(api, DOC=DOCS2, db_name='uruk')

<Response [201]>
Documents uploaded
